In [12]:
import os
import pandas as pd
import matplotlib.pyplot as plt

import folium
import geopandas as gpd

from shapely.geometry import Point

os.listdir('data')

['1.오산시_주정차단속(2018~2020).csv',
 '10.오산시_학교위치정보.csv',
 '11.오산시_초등학교_통학구.geojson',
 '12.오산시_중학교_학군.geojson',
 '13.오산시_어린이집_유치원현황.csv',
 '14.오산시_기상데이터(2010~2019).csv',
 '15.오산시_무인교통단속카메라.csv',
 '16.오산시_도로안전표지표준데이터.csv',
 '17.오산시_횡단보도.geojson',
 '18.오산시_과속방지턱표준데이터.csv',
 '19.오산시_신호등.geojson',
 '20.오산시_CCTV설치현황.csv',
 '21.오산시_인도.geojson',
 '22.오산시_버스정류장.csv',
 '27.오산시_도로명주소_건물.geojson',
 '28.오산시_건물연면적_격자.geojson',
 '29.오산시_체육시설현황.csv',
 '3.오산시_차량등록현황_격자.geojson',
 '30.오산시_학원 및 교습소 현황.csv',
 '31.오산시_법정경계(시군구).geojson',
 '32.오산시_행정경계(읍면동).geojson',
 '33.오산시_법정경계(읍면동).geojson',
 '34.오산시_지적도.geojson',
 '35.코드정의서.xlsx',
 '4.오산시_연령별_거주인구격자(총인구).geojson',
 '5.오산시_연령별_거주인구격자(유소년).geojson',
 '6.오산시_연령별_거주인구격자(생산가능인구).geojson',
 '7.오산시_연령별_거주인구격자(고령).geojson',
 '9.오산시_어린이보호구역.csv']

##### data 9 , data30 활용

In [39]:
from shapely.geometry import Point

data9 = pd.read_csv('data/9.오산시_어린이보호구역.csv')
data30 = pd.read_csv('data/30.오산시_학원 및 교습소 현황.csv')


def csv_to_geoframe(df, long_col, lat_col):
    df['geometry'] = df.apply(lambda row : Point([row[long_col], row[lat_col]]), axis=1)
    df = gpd.GeoDataFrame(df, geometry='geometry')
    
    return df

data9 = csv_to_geoframe(df = data9, long_col = '보호구역_경도', lat_col = '보호구역_위도')
data30 = csv_to_geoframe(df = data30, long_col = '시설위치_경도', lat_col = '시설위치_위도')


#반경을 설정해서 , buffer 생성
data9['geometry'] = data9['geometry'].buffer(0.001) 
data30['geometry'] = data30['geometry'].buffer(0.001)

display(data9.tail(2))
display(data30.tail(2))

시설종류         시설명 CCTV설치여부  CCTV설치대수  보호구역도로폭     보호구역_경도    보호구역_위도  \
89  어린이집     설리반어린이집        N         0        5  127.061041  37.164127   
90  어린이집  세교복지타운어린이집        Y         1       15  127.044835  37.177752   

                                             geometry  
89  POLYGON ((127.06204 37.16413, 127.06204 37.164...  
90  POLYGON ((127.04584 37.17775, 127.04583 37.177...

업종구분명  교습과정명     시설위치_경도    시설위치_위도  \
1784  학교교과교습학원  피아노초급  127.062722  37.165033   
1785  학교교과교습학원  체르니30  127.086780  37.142726   

                                               geometry  
1784  POLYGON ((127.06372 37.16503, 127.06372 37.164...  
1785  POLYGON ((127.08778 37.14273, 127.08777 37.142...

In [64]:
data9json = data9.to_json()
data30json = data30.to_json()




# 기본 맵 Setting
m = folium.Map(
    location=[37.16413,127.08104],
    zoom_start=13
)


#오산시 법정동 경계 표시
data33 = gpd.read_file('data/33.오산시_법정경계(읍면동).geojson') 
folium.GeoJson(data33).add_to(m) 




#오산시 어린이 보호구역
style1 = {'fillColor': '#000000', 'lineColor': '#ffffbf'}    

folium.GeoJson(
    data9json,
    style_function = lambda x: style1
).add_to(m)



#오산시 학원 및 교습소 현황
style2 = {'fillColor': '#fff000', 'lineColor': '#111111'}    

folium.GeoJson(
    data30json,
    style_function = lambda x: style2
).add_to(m)

m

C:\anaconda3\lib\site-packages\pyproj\crs\crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  return _prepare_from_string(" ".join(pjargs))


> 진행 필요한 사항
>- buffer 반경 변경 및 ,  Line 색상 변경 진행
>- grid 와 겹치는 개수 및 score 산정

In [8]:
from osgeo import ogr